# Assíncrono

Nesta seção o equacionamento realizado considerou a aplicação de uma força rotativa assíncrona excitando o sitema conforme proposto no livro texto da disciplina, "Rotordynamics Prediction in Engineering, Second Edition", {cite:ts}`lalanne_rotordynamics_1998`.

Foram calculadas as amplitudes de vibração em função da velocidade de rotação

## Importando módulos e configurando o ambiente

In [1]:
'''
    Módulos standard
'''
from collections import namedtuple

'''
    Bibliotecas de terceira parte
'''
import numpy as np

'''
    Biblioteca criada para a realização das análises dinâmicas
    no contexto da disciplina
'''
import rotor_analysis as rd

'''
    Configurando pint.Quantity
'''
Q_ = rd.Q_

## Adicionando assimetria ao modelo

In [2]:
import pint

class Spring():
    def __init__(self, coordinate:pint.Quantity, kxx:float=None, kzz:float=None):
        self.coordinate = coordinate
        if kxx:
            self.kxx = kxx
        else:
            self.kxx = Q_(0, "N/m")
        if kzz:
            self.kzz = kzz
        else:
            self.kzz = Q_(0, "N/m")

## Definindo parâmetros

In [3]:
# Material instances and properties
steel = rd.Material(name='Steel',
                    density=Q_(7800, 'kg/m^3'),
                    young_modulus=Q_(2e11,"Pa"))

# Shaft
L = Q_(0.4, 'm')
shaft = rd.Shaft(outer_radius=Q_(0.01, 'm'),
                 inner_radius=Q_(0.0, 'm'),
                 length=L,
                 material=steel)

# Spring
L2 = 2 * L / 3
kzz = Q_(5e5, "N/m")
spring = Spring(L2, kzz=kzz)

# Disc
disc = rd.Disc(outer_radius=Q_(0.150, 'm'),
               inner_radius=Q_(0.010, 'm'),
               length=Q_(0.030, 'm'),
               material=steel,
               coordinate=L/3)

# Rotor
rotor = rd.Rotor(shaft, disc, spring=spring)
speed_range = np.linspace(0, 9000, 101)

In [4]:
def A1_async(speed, *args):
    '''Compute the displacemente aplitude of the rotor with an asynchronous 
    excitation.
    
    Args:
        speed (function): Rotational speed in RPM.
        F0 (float): Asynchronous force magnitude
        s (float): A multiplier thats desynchronize the excitation

    Remarks:
        len(args) shall be equals to 2
    '''
    F0, s = args
    k1, k2 = rotor.stiffness
    m = rotor.mass
    spin = speed / 60 * 2 * np.pi
    a = rotor.a
    div = s**2 * (s**2 * m**2 - a**2) * spin**4 - m * (k1 + k2) * s**2 * spin**2 + k1 * k2
    return (k2 - (m * s**2 + a * s) * spin**2) * F0 / div

def A2_async(speed, *args):
    '''Compute the displacemente aplitude of the rotor with an asynchronous 
    excitation.
    
    Args:
        speed (function): Rotational speed in RPM.
        F0 (float): Asynchronous force magnitude
        s (float): A multiplier thats desynchronize the excitation

    Remarks:
        len(args) shall be equals to 2
    '''
    F0, s = args
    k1, k2 = rotor.stiffness
    m = rotor.mass
    spin = speed / 60 * 2 * np.pi
    a = rotor.a
    div = s**2 * (s**2 * m**2 - a**2) * spin**4 - m * (k1 + k2) * s**2 * spin**2 + k1 * k2
    return (k1 - (m * s**2 + a * s) * spin**2) * F0 / div


In [5]:
# Computing the values
values = []
s = 0.5
for speed in speed_range:
    A1 = abs(A1_async(speed, 1, s))
    A2 = abs(A2_async(speed, 1, s))
    values.append(max(A1, A2))

# Generating the Standard Campbell Diagram
campbell_fig = rotor.plot_Campbell()

# Call the function to add the secondary y-axis
rd.add_secondary_yaxis(campbell_fig, values)

#adjusting the legend
campbell_fig.update_layout(
    legend=dict(yanchor="top", y=0.99, xanchor="left", x=0.01),
)

orbit_plot = rd.interactive_orbit_campbell(campbell_fig,
                                           A1_async,
                                           A2_async,
                                           1,
                                           0.5,
                                           initial_speed=2700)
#adjusting the legend
orbit_plot.update_layout(
    legend=dict(yanchor="top", y=0.5, xanchor="left", x=0.01),
)

# Show the updated figure
orbit_plot.show()